<a href="https://colab.research.google.com/github/ramsrigouthamg/Supertranslate.ai/blob/main/Scrolling_Subtitles_On_Video_using_Python/Scrolling_Subtitles_On_Video_using_Python.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

Code and files for this notebook: https://github.com/aeronesto/youtube

Author: [Ernesto Jimenez](https://x.com/aeronestoTM)

In [1]:
!pip install --upgrade openai-whisper


[notice] A new release of pip is available: 24.2 -> 24.3.1
[notice] To update, run: pip install --upgrade pip


## Step1: Define input videos and image files

In [2]:
# The audio you want in the final video (original song)
desired_audio = "inputs/original.m4a"

# The audio to transcribe (vocals only)
audio_to_transcribe = "inputs/vocals.mp3"

# The background image for final video
image_filename = "inputs/background_image.png"

# The instrumental version of the song for karaoke
instrumental_audio_path = "inputs/instrumental.mp3"

# The time delta when transcription is off
dt = 0

# The lyrics to the song (helps get very accurate transcription)
lyrics = """I'm rememberin' I promised to forget you now But it's rainin' and I'm callin' drunk And my medicine is drownin' your perspective out So I ain't takin' any fault Am I honest still? Am I half the man I used to be? I doubt it, forget about it, whatever It's all the same anyways I ain't proud of all the punches that I've thrown In the name of someone I no longer know For the shame of bein' young, drunk, and alone Traffic lights and a transmitter radio I don't like that when they threw me in the car I gave your name as my emergency phone call Honey, it rang and rang Even the cops thought you were wrong for hangin' up I dial drunk, I'll die a drunk, I'd die for you I'm untetherin' from the parts of me you'd recognize From charmin' to alarmin' in seconds I'll be bedridden, I'll let the pain metastasize But that's morning, I'll forget it And the dial tone is all I have You might also like I ain't proud of all the punches that I've thrown In the name of someone I no longer know For the shame of bein' young, drunk, and alone Traffic lights and a transmitter radio I don't like that when they threw me in the car I gave your name as my emergency phone call Honey, it rang and rang Even the cops thought you were wrong for hangin' up I dial drunk, I'll die a drunk, I'd die for you Well, I'd die for you I beg you, sir, just let me call I'll give you my blood alcohol I'll rot with all the burnouts in the cell I'll change my faith, I'll praise the flag Let's wait, I swear she'll call me back "Son, are you a danger to yourself?" Fuck that, sir, just let me call I'll give you my blood alcohol I'll rot with all the burnouts in the cell I'll change my faith, I'll kiss the badge Let's wait, I swear she'll call me back "Son, why do you do this to yourself?" And I said I ain't proud of all the punches that I've thrown In the name of someone I no longer know (I no longer know) For the shame of bein' young, drunk, and alone Traffic lights and a transmitter radio I don't like that when they threw me in the car I gave your name as my emergency phone call Honey, it rang and rang Even the cops thought you were wrong for hangin' up I dial drunk, I'll die a drunk, I'd die for you"""

## Step2: Extract audio (mp3) from the video file

In [3]:
import os
from pydub import AudioSegment
from datetime import datetime
current_time = datetime.now().strftime("%y-%m-%d-%H-%M-%S")

just_the_filename = os.path.splitext(os.path.basename(desired_audio))[0]
sans_extension = f"outputs/{current_time}-{just_the_filename}"

# export .aac audio to .mp3
if audio_to_transcribe.endswith('.aac'):
    # Load the .aac file
    audio = AudioSegment.from_file(audio_to_transcribe, format="aac")

    # Export it as an .mp3 file
    audio.export(audio_to_transcribe.replace(".aac",".mp3"), format="mp3")

In [4]:
!pip install ffmpeg-python==0.2.0


[notice] A new release of pip is available: 24.2 -> 24.3.1
[notice] To update, run: pip install --upgrade pip


In [5]:
import ffmpeg

if desired_audio.endswith(('.mp4','.m4a')):

    # Create the ffmpeg input stream
    input_stream = ffmpeg.input(desired_audio)

    # Extract the audio stream from the input stream
    audio = input_stream.audio

    # mp3 file path
    desired_audio = f"{sans_extension}.mp3"

    # Save the audio stream as an MP3 file
    output_stream = ffmpeg.output(audio, desired_audio)

    # Overwrite output file if it already exists
    output_stream = ffmpeg.overwrite_output(output_stream)

    ffmpeg.run(output_stream)

ffmpeg version 7.1 Copyright (c) 2000-2024 the FFmpeg developers
  built with Apple clang version 15.0.0 (clang-1500.3.9.4)
  configuration: --prefix=/opt/homebrew/Cellar/ffmpeg/7.1 --enable-shared --enable-pthreads --enable-version3 --cc=clang --host-cflags= --host-ldflags='-Wl,-ld_classic' --enable-ffplay --enable-gnutls --enable-gpl --enable-libaom --enable-libaribb24 --enable-libbluray --enable-libdav1d --enable-libharfbuzz --enable-libjxl --enable-libmp3lame --enable-libopus --enable-librav1e --enable-librist --enable-librubberband --enable-libsnappy --enable-libsrt --enable-libssh --enable-libsvtav1 --enable-libtesseract --enable-libtheora --enable-libvidstab --enable-libvmaf --enable-libvorbis --enable-libvpx --enable-libwebp --enable-libx264 --enable-libx265 --enable-libxml2 --enable-libxvid --enable-lzma --enable-libfontconfig --enable-libfreetype --enable-frei0r --enable-libass --enable-libopencore-amrnb --enable-libopencore-amrwb --enable-libopenjpeg --enable-libspeex --enab

In [6]:
from IPython.display import Audio

Audio(desired_audio)

## Step3: Get word-level transcription (speech-to-text) from audio using OpenAI's Whisper

In [7]:
import whisper

model_size = "medium"
model = whisper.load_model(model_size)

/Users/erniej/Documents/dev/youtube/venv/lib/python3.12/site-packages/whisper/__init__.py:150: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  checkpoint = torch.load(fp, map_

In [ ]:
result = model.transcribe(audio_to_transcribe, word_timestamps=True, initial_prompt=lyrics)
text = result['text']
segments = result['segments']

/Users/erniej/Documents/dev/youtube/venv/lib/python3.12/site-packages/whisper/transcribe.py:126: UserWarning: FP16 is not supported on CPU; using FP32 instead
  warnings.warn("FP16 is not supported on CPU; using FP32 instead")
OMP: Info #276: omp_set_nested routine deprecated, please use omp_set_max_active_levels instead.


In [ ]:
from types import SimpleNamespace

In [ ]:
for segment in segments:
    segment_obj = SimpleNamespace(**segment)
    for word in segment_obj.words:
        word_obj = SimpleNamespace(**word)
        print("[%.2fs -> %.2fs] %s" % (word_obj.start, word_obj.end, word_obj.word))

In [ ]:
wordlevel_info = []

for segment in segments:
    for word_dict in segment['words']:
      word = SimpleNamespace(**word_dict)
      wordlevel_info.append({'word':word.word,'start':word.start-dt,'end':word.end-dt})


In [ ]:
wordlevel_info

## Step4: Create a simple UI to edit any errors

In [ ]:
from ipywidgets import widgets
from IPython.display import display

In [ ]:
# Create a table to display the wordlevel_info
table_columns = ['Start', 'End', 'Word']
# Create the table rows
table_rows = []

for word_info in wordlevel_info:
    start_widget = widgets.Text(value=str(word_info['start']))
    end_widget = widgets.Text(value=str(word_info['end']))
    word_widget = widgets.Text(value=word_info['word'])
    row_widgets = widgets.HBox([start_widget, end_widget, word_widget])
    table_rows.append(row_widgets)


# Create the update button
button = widgets.Button(description='Update')

# Create the output area for displaying the updated wordlevel_info
output_area = widgets.Output()

In [ ]:
# Create a new variable to store the modified wordlevel_info
modified_wordlevel_info = []

def update_wordlevel_info(event):
    with output_area:
        output_area.clear_output()
        updated_wordlevel_info = []

        for row_widgets in table_rows:
            start = float(row_widgets.children[0].value)  # Convert start to float
            end = float(row_widgets.children[1].value)  # Convert end to float
            word = row_widgets.children[2].value.strip()
            updated_wordlevel_info.append({'start': start, 'end': end, 'word': word})

        # Print the updated wordlevel_info
        print(updated_wordlevel_info)

        # Assign updated_wordlevel_info to modified_wordlevel_info
        # global modified_wordlevel_info
        modified_wordlevel_info = updated_wordlevel_info

button.on_click(update_wordlevel_info)




In [ ]:
# Create the table widget
table_widget = widgets.VBox(table_rows)

# Display the UI elements
display(table_widget, button, output_area)


In [ ]:
modified_wordlevel_info = wordlevel_info
# modified_wordlevel_info

## Step5: Store word-level timestamps into JSON file

In [ ]:
import json
subtitles_json_path = f'{sans_extension}.json'
with open(subtitles_json_path, 'w') as f:
    json.dump(modified_wordlevel_info, f,indent=4)

## Step6: Load edits to word-level timestamps

In [ ]:
import json
subtitles_json_path = f'{sans_extension}.json'
with open(subtitles_json_path, 'r') as f:
    wordlevel_info_modified = json.load(f)


In [ ]:
wordlevel_info_modified

## Step6: Convert word-level timestamps JSON to line-level timestamps JSON. We want to display one line at a time and highlight words in it as they are spoken so we do this transformation.

In [ ]:
def split_text_into_lines(data):

    # max characters
    MaxChars = 100
    
    #maxduration in seconds
    MaxDuration = 10
    
    #Split if nothing is spoken (gap) for these many seconds
    MaxGap = 0.25

    subtitles = []
    line = []
    line_duration = 0

    current_gap = 0

    for idx,word_data in enumerate(data):
        start = word_data["start"]
        end = word_data["end"]
        
        # time gap between words
        current_gap = word_data['start'] - data[idx-1]['end'] if idx > 0 else 0
        maxgap_exceeded = current_gap > MaxGap
        
        # current phrase duration
        line_duration += end - start
        # Check if the line duration is longer than allowed
        duration_exceeded = line_duration > MaxDuration
        
        # characters per line
        temp = " ".join([*[item["word"] for item in line], word_data['word']])
        new_line_chars = len(temp)
        # Check if adding a new word exceeds the maximum character count
        chars_exceeded = new_line_chars > MaxChars
        
        if duration_exceeded or chars_exceeded or maxgap_exceeded:
            # current word can't go in current line
            if line:
                # if words exist in current line, end the line
                subtitle_line = {
                    "word": " ".join(item["word"] for item in line),
                    "start": line[0]["start"],
                    "end": line[-1]["end"],
                    "textcontents": line
                }
                subtitles.append(subtitle_line)

            # define the start of the next line
            line = [word_data]
            line_duration = end - start
        else:
            line.append(word_data)

    if line:
        subtitle_line = {
            "word": " ".join(item["word"] for item in line),
            "start": line[0]["start"],
            "end": line[-1]["end"],
            "textcontents": line
        }
        subtitles.append(subtitle_line)

    return subtitles

In [ ]:
linelevel_subtitles = split_text_into_lines(wordlevel_info_modified)

In [ ]:
for line in linelevel_subtitles:
    print("[%.2fs -> %.2fs] %s" % (line['start'], line['end'], line['word']))

## Step7: Use Moviepy to create an audiogram with word-level highlights as they are spoken

In [ ]:
from moviepy.editor import TextClip, CompositeVideoClip


def create_captioned_video(textJSON, framesize,font = "Fancake",color='white', highlight_color='yellow',stroke_color='black',stroke_width=1.5):
    full_duration = textJSON['end']-textJSON['start']

    word_clips = []
    xy_textclips_positions =[]

    x_pos = 0
    y_pos = 0
    line_width = 0  # Total width of words in the current line
    frame_width = framesize[0]
    frame_height = framesize[1]

    x_buffer = frame_width*1/10

    max_line_width = frame_width - 2 * (x_buffer)

    fontsize = int(frame_height * 0.075) #7.5 percent of video height

    space_width = ""
    space_height = ""

    for index,wordJSON in enumerate(textJSON['textcontents']):
      duration = wordJSON['end']-wordJSON['start']
      word_clip = TextClip(wordJSON['word'], font = font,fontsize=fontsize, color=color,stroke_color=stroke_color,stroke_width=stroke_width).set_start(textJSON['start']).set_duration(full_duration)
      word_clip_space = TextClip(" ", font = font,fontsize=fontsize, color=color).set_start(textJSON['start']).set_duration(full_duration)
      word_width, word_height = word_clip.size
      space_width,space_height = word_clip_space.size
      if line_width + word_width+ space_width <= max_line_width:
            # Store info of each word_clip created
            xy_textclips_positions.append({
                "x_pos":x_pos,
                "y_pos": y_pos,
                "width" : word_width,
                "height" : word_height,
                "word": wordJSON['word'],
                "start": wordJSON['start'],
                "end": wordJSON['end'],
                "duration": duration
            })

            word_clip = word_clip.set_position((x_pos, y_pos))
            word_clip_space = word_clip_space.set_position((x_pos+ word_width, y_pos))

            x_pos = x_pos + word_width+ space_width
            line_width = line_width+ word_width + space_width
      else:
            # Move to the next line
            x_pos = 0
            y_pos = y_pos+ word_height+10
            line_width = word_width + space_width

            # Store info of each word_clip created
            xy_textclips_positions.append({
                "x_pos":x_pos,
                "y_pos": y_pos,
                "width" : word_width,
                "height" : word_height,
                "word": wordJSON['word'],
                "start": wordJSON['start'],
                "end": wordJSON['end'],
                "duration": duration
            })

            word_clip = word_clip.set_position((x_pos, y_pos))
            word_clip_space = word_clip_space.set_position((x_pos+ word_width , y_pos))
            x_pos = word_width + space_width


      word_clips.append(word_clip)
      if index < len(textJSON['textcontents']) - 1:
        word_clips.append(word_clip_space)


    for highlight_word in xy_textclips_positions:

      word_clip_highlight = TextClip(highlight_word['word'], font = font,fontsize=fontsize, color=highlight_color,stroke_color=stroke_color,stroke_width=stroke_width).set_start(highlight_word['start']).set_duration(highlight_word['duration'])
      word_clip_highlight = word_clip_highlight.set_position((highlight_word['x_pos'], highlight_word['y_pos']))
      word_clips.append(word_clip_highlight)

    return word_clips,xy_textclips_positions

## Create video from image

In [ ]:
## Imports
import moviepy.editor as mp
from moviepy.editor import ImageClip
import os

def create_video_from_image(input_audio_path, input_image_path):
    tmp_path = "./scripts/subtitle_videos/tmp"
    os.makedirs(tmp_path, exist_ok=True)

    # Load audio
    audio_clip = mp.AudioFileClip(input_audio_path)

    # Create video with input image
    image_clip = ImageClip(input_image_path, duration=audio_clip.duration).set_fps(30)
    
    # create final video of image with subtitles and original audio
    final_clip = CompositeVideoClip([image_clip])

    # final_clip = ImageClip(input_image_path, duration=audio_clip.duration).set_fps(30)

    final_clip = final_clip.set_audio(audio_clip)
    
    # final_clip.write_videofile(f'{sans_extension}.mp4', fps=30, remove_temp=True, codec="libx264", audio_codec="aac")
    
    return final_clip

## Step8: Create lyric video

In [ ]:
from moviepy.editor import TextClip, CompositeVideoClip, concatenate_videoclips,VideoFileClip, ColorClip
input_video = create_video_from_image(desired_audio, image_filename)
frame_size = input_video.size

all_linelevel_splits=[]

for line in linelevel_subtitles:
  out_clips,positions = create_captioned_video(line,frame_size)

  max_width = 0
  max_height = 0

  for position in positions:
    x_pos, y_pos = position['x_pos'],position['y_pos']
    width, height = position['width'],position['height']

    max_width = max(max_width, x_pos + width)
    max_height = max(max_height, y_pos + height)

  color_clip = ColorClip(size=(int(max_width*1.1), int(max_height*1.1)),
                       color=(29, 79, 129))
  color_clip = color_clip.set_opacity(.6)
  color_clip = color_clip.set_start(line['start']).set_duration(line['end']-line['start'])

  clip_to_overlay = CompositeVideoClip([color_clip]+ out_clips)
  clip_to_overlay = clip_to_overlay.set_position("center")


  all_linelevel_splits.append(clip_to_overlay)

input_video_duration = input_video.duration


final_video = CompositeVideoClip([input_video] + all_linelevel_splits)

# Set the audio of the final video to be the same as the input video
final_video = final_video.set_audio(input_video.audio)

In [ ]:
# Save the final clip as a video file with the audio included
# final_video.write_videofile(f"/Users/erniej/Documents/dev/youtube/scripts/subtitle_videos/tmp/{current_time}-output.mp4", fps=input_video.fps, codec="libx264", audio_codec="aac")
output_file_path = f"{sans_extension}.mp4"
final_video.write_videofile(output_file_path, fps=final_video.fps, remove_temp=True, codec="libx264", audio_codec="aac")

### Display video

In [ ]:
from IPython.display import HTML
from base64 import b64encode
mp4 = open(output_file_path,'rb').read()
data_url = "data:video/mp4;base64," + b64encode(mp4).decode()
HTML("""
<video width=600 controls>
      <source src="%s" type="video/mp4">
</video>
""" % data_url)

## Step9: Create karaoke video

In [ ]:
if instrumental_audio_path.endswith('.aac'):
    # Load the .aac file
    audio = AudioSegment.from_file(instrumental_audio_path, format="aac")

    # Export it as an .mp3 file
    instrumental_audio_path = instrumental_audio_path.replace(".aac",".mp3")
    audio.export(instrumental_audio_path, format="mp3")

instrumental_input_video = create_video_from_image(instrumental_audio_path, image_filename)
instrumental_video = CompositeVideoClip([instrumental_input_video] + all_linelevel_splits)
instrumental_video = instrumental_video.set_audio(instrumental_input_video.audio)

# Save the final clip as a video file with the audio included
output_file_path = f"{sans_extension}-instrumental.mp4"

instrumental_video.write_videofile(output_file_path, fps=instrumental_video.fps, remove_temp=True, codec="libx264", audio_codec="aac")

## Extra - Check all fonts available

In [ ]:
# from moviepy.editor import TextClip

# # Create a dummy TextClip object
# dummy_clip = TextClip('Dummy Text')

# # Get the available fonts
# available_fonts = dummy_clip.list('font')

# # Print the available fonts
# for font in available_fonts:
#     print(font)
